In [108]:
#Data Reduction

import pandas as pd
import numpy as np
import plotly.graph_objs as go
import plotly.offline as pyo 
import CoolProp.CoolProp as CP


# CS4_V1 VALUES
Lf = 120/1000 # mm Length of the core
Vf_cs4 = 13190 * 1e-9 #m³  Volume of the fluid in core
Afs_cs4 = 35459 * 1e-6 #m² Interfacial surface area between fluid/wall
Acs_cs4 = Vf_cs4 / Lf
Dh_cs4 = (4*Vf_cs4)/Afs_cs4

#CS6_V1 VALUES
Lf = 120/1000 # mm Length of the core
Vf_cs6 = 17310 * 1e-9 #m³  Volume of the fluid in core
Afs_cs6 = 24953 * 1e-6 #m² Interfacial surface area between fluid/wall
Acs_cs6 = Vf_cs6 / Lf
Dh_cs6 = (4*Vf_cs6)/Afs_cs6

#CS8_V1 VALUES
Lf = 120/1000 # m Length of the core
Vf_cs8 = 19478 * 1e-9 #m³  Volume of the fluid in core
Afs_cs8 = 18843 * 1e-6 #m² Interfacial surface area between fluid/wall
Acs_cs8 = Vf_cs8 / Lf
Dh_cs8 = (4*Vf_cs8)/Afs_cs8

#CS10_V1 VALUES
Lf = 120/1000 # m Length of the core
Vf_cs10 = 20892 * 1e-9 #m³  Volume of the fluid in core
Afs_cs10 = 15415 * 1e-6 #m² Interfacial surface area between fluid/wall
Acs_cs10 = Vf_cs10 / Lf
Dh_cs10 = (4*Vf_cs10)/Afs_cs10

#CS12_V1 VALUES
Lf = 120/1000 # m Length of the core
Vf_cs12 = 21921 * 1e-9 #m³  Volume of the fluid in core
Afs_cs12 = 12935 * 1e-6 #m² Interfacial surface area between fluid/wall
Acs_cs12 = Vf_cs12 / Lf
Dh_cs12 = (4*Vf_cs12)/Afs_cs12

#CS15_V1 VALUES
Lf = 120/1000 # m Length of the core
Vf_cs15 = 22417 * 1e-9 #m³  Volume of the fluid in core
Afs_cs15 = 10438 * 1e-6 #m² Interfacial surface area between fluid/wall
Acs_cs15 = Vf_cs15 / Lf
Dh_cs15 = (4*Vf_cs15)/Afs_cs15

# DEFINING REYNOLDS AND VELOCITY
T = 300
mu = CP.PropsSI('V', 'T', T, 'P', 101325, 'Water')
rho = CP.PropsSI('D', 'T', 300, 'P', 101325, 'Water')


def Reynolds(mfr, dh, acs, mu):
    Re = (mfr * dh) / (acs * mu)
    return Re 

def Reynolds(rho, v, dh, mu):
    Re = (rho * v * dh) / (mu)
    return Re 

def Velocity(mfr, rho, acs):
    Vel = (mfr) / (rho * acs)
    return Vel

def ffactor(dp, dh, L, rho, V):
    f = (dp * dh) / (2*L*rho*(np.power(V,2)))
    return f

In [109]:
# DATA READ - REYNOLDS AND VELOCITY VALUES

import pandas as pd
import plotly.graph_objs as go
import plotly.offline as pyo
import tensorflow as tf
from tensorflow.keras import regularizers
import numpy as np
import plotly.io
from sklearn.utils import shuffle
#import data, X = inputs, Y = outputs 
df = pd.read_excel('Data.xlsx')
df = shuffle(df)#embaralha os dados



X = df.iloc[:,[1,2]].values
Y = df.iloc[:, 0].values.reshape(-1,1) * 100000


In [110]:


#Parameter control
trainsize = 0.4
neurons = 4
activation_function = 'relu'
batchsize = 32
epochs = 250
hidden_layers_quantity = 2

#normalize data
from sklearn.preprocessing import StandardScaler
scalerx = StandardScaler()
scalery = StandardScaler()
X_scaled = scalerx.fit_transform(X)
Y_scaled = scalery.fit_transform(Y)

#split data  
#from sklearn.model_selection import train_test_split

#Xtrain, Xtest, Ytrain, Ytest = train_test_split(X_scaled, Y_scaled, 
#                                                train_size = trainsize, 
#                                                random_state = 0)

#using K-fold to split the data
from sklearn.model_selection import KFold
kf = KFold(n_splits = 10)


In [111]:
#Building the ANN MODEL
#aplicar knn regressor, média e desvio padrão de r2 e msr
from sklearn.metrics import r2_score, mean_squared_error

resultados = []
fold  = 0

for train, test in kf.split(X_scaled):
    fold+=1

    Xtrain = X_scaled[train]
    Ytrain = Y_scaled[train]

  
    #gridsearchcv aplicar no xtrain ytrain
    Ytest = Y_scaled[test]
    Xtest = X_scaled[test]

In [112]:
print(Ytrain)

[[-1.03004175]
 [-0.54853145]
 [-0.94079911]
 ...
 [-1.08796343]
 [-1.08519639]
 [ 0.00733995]]


In [113]:
#Building the ANN MODEL
from sklearn.metrics import r2_score, mean_squared_error

resultados = []
fold  = 0

for train, test in kf.split(X_scaled):
    fold+=1

    Xtrain = X_scaled[train]
    Ytrain = Y_scaled[train]

  
    #gridsearchcv aplicar no xtrain ytrain
    Ytest = Y_scaled[test]
    Xtest = X_scaled[test]

    # pega ros melhores parametros de resultado do gridsearchcv e treinar a rede com todos os dados de treino
    parametros = []

    for neurons in range(1, neurons+1):

        for hidden_layers_quantity in range (1, hidden_layers_quantity+1):

            ann = tf.keras.models.Sequential() #Initializethe ann model

            #creatin a sequence of hidden layers (adding according to the range)
            for _ in range(hidden_layers_quantity):
                ann.add(tf.keras.layers.Dense(units=neurons, 
                                            activation=activation_function))                        
                ann.add(tf.keras.layers.Dropout(0.2)) #DROPUT LAYER

            ann.add(tf.keras.layers.Dense(units = 1)) # OUTPUT LAYER

            #Compiling the ann, it adds the stochastic gradient descent method to control losses
            ann.compile(optimizer = 'adam', 
                        loss = 'mean_squared_error') #COMPILER (TRY DIFFERENT PARAMETERS)

            #TRAIN THE ANN MODEL
            ann.fit(Xtrain, Ytrain, 
                    batch_size = batchsize, 
                    epochs = epochs)
            Qpred = ann.predict(Xtest)
            
            rmse = mean_squared_error(Ytest, Qpred, squared = False)
            r2 = r2_score(Ytest, Qpred)
            resultados.append((fold, neurons, hidden_layers_quantity, rmse, r2))
            

        #salvar dados de loss de treino e teste durante a ann


Epoch 1/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 1s 581us/step - loss: 2.4642 
Epoch 2/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 528us/step - loss: 1.8377
Epoch 3/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 519us/step - loss: 1.5504
Epoch 4/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 536us/step - loss: 1.3229
Epoch 5/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 532us/step - loss: 1.2713
Epoch 6/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 516us/step - loss: 1.1983
Epoch 7/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 527us/step - loss: 1.1489
Epoch 8/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 511us/step - loss: 1.1832
Epoch 9/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 522us/step - loss: 1.1484
Epoch 10/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 526us/step - loss: 1.1009
Epoch 11/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 555us/step - loss: 1.0883
Epoch 12/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 541us/step - loss: 1.0939
Epoch 13/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 535us/step - loss: 1.0040
Epoch 14/250
108/108 ━━━━━━━━━━━━━━━━━━━━ 0s 535us/step - loss: 1.0249
Epoch 15/250
1

In [114]:
print(resultados)

[(1, 1, 1, 0.9758933258398286, -0.001613723311585602), (1, 1, 2, 0.9758476125846675, -0.001519889385057649), (1, 2, 1, 0.43311912160305166, 0.8027076318277416), (1, 2, 2, 0.688084770813987, 0.5020571941075332), (1, 3, 1, 0.3409856923841596, 0.8777164935094753), (1, 3, 2, 0.48866962782913204, 0.7488540002773348), (1, 4, 1, 0.2817329856405813, 0.9165222055918175), (1, 4, 2, 0.3841932851568545, 0.8447630466669558), (2, 1, 1, 0.46782192520783916, 0.7865534772100901), (2, 1, 2, 0.7548185343032412, 0.4443349882558263), (2, 2, 1, 0.6543959983965248, 0.5823531497271572), (2, 2, 2, 0.7122596364951541, 0.5052285767019238), (2, 3, 1, 0.34993623592748296, 0.880572106381549), (2, 3, 2, 0.5085074509699654, 0.7478130656792188), (2, 4, 1, 0.314929796229952, 0.9032712791024001), (2, 4, 2, 0.38302211440565465, 0.8569210846155559), (3, 1, 1, 0.5722694452617922, 0.6306789001302762), (3, 1, 2, 0.9418728557125885, -0.0004319775789298763), (3, 2, 1, 0.9418358819732033, -0.0003534341004520769), (3, 2, 2, 0.49

In [115]:
# RMSE: 0, R2:1
for result in resultados:
    print(f"FOLD{result[0]} -  Para {result[1]} neurônios e {result[2]} camadas, RMSE = {result[3]}, R2 = {result[4]}")


FOLD1 -  Para 1 neurônios e 1 camadas, RMSE = 0.9758933258398286, R2 = -0.001613723311585602
FOLD1 -  Para 1 neurônios e 2 camadas, RMSE = 0.9758476125846675, R2 = -0.001519889385057649
FOLD1 -  Para 2 neurônios e 1 camadas, RMSE = 0.43311912160305166, R2 = 0.8027076318277416
FOLD1 -  Para 2 neurônios e 2 camadas, RMSE = 0.688084770813987, R2 = 0.5020571941075332
FOLD1 -  Para 3 neurônios e 1 camadas, RMSE = 0.3409856923841596, R2 = 0.8777164935094753
FOLD1 -  Para 3 neurônios e 2 camadas, RMSE = 0.48866962782913204, R2 = 0.7488540002773348
FOLD1 -  Para 4 neurônios e 1 camadas, RMSE = 0.2817329856405813, R2 = 0.9165222055918175
FOLD1 -  Para 4 neurônios e 2 camadas, RMSE = 0.3841932851568545, R2 = 0.8447630466669558
FOLD2 -  Para 1 neurônios e 1 camadas, RMSE = 0.46782192520783916, R2 = 0.7865534772100901
FOLD2 -  Para 1 neurônios e 2 camadas, RMSE = 0.7548185343032412, R2 = 0.4443349882558263
FOLD2 -  Para 2 neurônios e 1 camadas, RMSE = 0.6543959983965248, R2 = 0.5823531497271572
FO

In [116]:
#apply inverse transform on the Xtest and Ytest
Xtest_original = scalerx.inverse_transform(Xtest)
Ytest_original = scalery.inverse_transform(Ytest)

vel = Velocity()

#predict function
Qpred = ann.predict(Xtest)
Qpred_original = scalery.inverse_transform(Qpred)

print(Xtest_original)

12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 773us/step
[[0.05942 0.2495 ]
 [0.05024 0.4331 ]
 [0.15696 0.4331 ]
 [0.05769 0.3996 ]
 [0.06163 0.3326 ]
 [0.08262 0.3745 ]
 [0.10445 0.4331 ]
 [0.08167 0.2495 ]
 [0.07414 0.3745 ]
 [0.10871 0.3996 ]
 [0.06381 0.2495 ]
 [0.05013 0.3996 ]
 [0.05665 0.2495 ]
 [0.09691 0.3745 ]
 [0.06751 0.3745 ]
 [0.08133 0.3996 ]
 [0.10398 0.4331 ]
 [0.0577  0.3745 ]
 [0.05865 0.4331 ]
 [0.09709 0.3326 ]
 [0.07369 0.3996 ]
 [0.08829 0.3745 ]
 [0.05039 0.3996 ]
 [0.04767 0.3745 ]
 [0.05824 0.2495 ]
 [0.15798 0.4331 ]
 [0.04784 0.2495 ]
 [0.07227 0.4331 ]
 [0.06586 0.3745 ]
 [0.06277 0.3996 ]
 [0.04242 0.4331 ]
 [0.0901  0.4331 ]
 [0.05845 0.3745 ]
 [0.04839 0.4331 ]
 [0.06129 0.2495 ]
 [0.04987 0.3326 ]
 [0.05774 0.2495 ]
 [0.1107  0.4331 ]
 [0.07327 0.2495 ]
 [0.08246 0.3745 ]
 [0.06234 0.3996 ]
 [0.07768 0.3326 ]
 [0.10117 0.4331 ]
 [0.10138 0.3326 ]
 [0.1125  0.3326 ]
 [0.0781  0.4331 ]
 [0.13446 0.4331 ]
 [0.09349 0.3996 ]
 [0.07759 0.3745 ]
 [0.06301 0.2495 ]
 [0.10994

In [118]:
x = Xtest_original[:,0]
y = Xtest_original[:,1]
z = Qpred_original[:,0]
print(z)

scatter = go.Scatter3d(x= x, y= y, z= z, mode = 'markers', marker=dict(size = 5, color = z, colorscale = 'Viridis', opacity = 0.8))
layout = go.Layout(
    title='Gráfico de Dispersão 3D',
    scene=dict(
        xaxis_title='Mass Flow Rate (kg/s)',
        yaxis_title='Standard Porosity',
        zaxis_title='dP (Pa)'
    )
)
fig = go.Figure( data = [scatter], layout=layout)
pyo.plot(fig)

[ 91791.484  40661.305  51663.402  40661.305  40661.305  40661.305
  40661.305 133228.73   40661.305  43204.664  99967.195  40661.305
  86632.78   45009.793  40661.305  40661.305  40661.305  40661.305
  40661.305  60141.92   40661.305  40661.305  40661.305  40661.305
  89593.914  51889.016  70225.49   40661.305  40661.305  40661.305
  40661.305  40661.305  40661.305  40661.305  95274.08   40661.305
  88662.74   40661.305 117585.01   40661.305  40661.305  48308.46
  40661.305  62757.355  73443.555  40661.305  46686.645  40661.305
  40661.305  98477.32   40661.305  94525.34   47440.9    40661.305
  40661.305  43674.64   65264.207  40661.305  60958.863 104231.97
  69194.92   49747.254  61659.555  40661.305  68340.72   49808.22
  61336.85   40661.305  55196.332  40661.305  40661.305  40760.477
  41899.52  106150.195  40661.305  40661.305  66646.555  58940.895
  49728.79   40661.305  40661.305  40661.305  40661.305  40661.305
  80930.2    51459.434  40661.305  60507.297  40661.305  46576.61

'temp-plot.html'